In this wonderful notebook I am going to do preprocessing of two datasets? daln.csv and amazon_cells_labelled.txt

Let's start with daln data 

In [1]:
#importing necessary libraries and the data itself
import pandas as pd
import numpy as np
daln_df = pd.read_csv('daln.csv', encoding='utf-8', sep='delimiter', engine = 'python')
num_rows, num_feature = daln_df.shape

In [2]:
daln_df.shape
#as we can see, the daln data has 369 rows and one column that is text

(369, 1)

In [3]:
daln_df.head() 

original data\tMeta1\tMeta2\tMeta3\tMeta4\tMeta5\tMeta6\tMeta7\tMeta8\tMeta9\tMeta10\tMeta11\tMeta12\tMeta13\tMeta14\tMeta15\tMeta16\tMeta17\tMeta18\tMeta19\tMeta20
0  Лидер движения  За права человека  Лев Пономар...                                                                                                                  
1  Здесь в нескольких километрах от города-сателл...                                                                                                                  
2  По результатам проверок будут приняты «объекти...                                                                                                                  
3  Посмотрите фотографию. Это   нижегородец Никол...                                                                                                                  
4  8 апреля  русская православная церковь праздну...

In [4]:
#it is also obvious that the name of the column with text is inaproppriate 
#it needs to be renamed for future convenience

daln_df0 = daln_df.rename(columns={daln_df.columns[0]: "text_original"})
daln_df0.head()

text_original
0  Лидер движения  За права человека  Лев Пономар...
1  Здесь в нескольких километрах от города-сателл...
2  По результатам проверок будут приняты «объекти...
3  Посмотрите фотографию. Это   нижегородец Никол...
4  8 апреля  русская православная церковь праздну...

In [5]:
#now I can start preprocessing
# in this chunk text is tokenized and lemmatized - the latter is done with pymorphy

import pymorphy2
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize

morph = pymorphy2.MorphAnalyzer()

import re
import time

x_data = []

daln_data = []

start = time.time()

for i in range (num_rows):
    doc_stem =''
    s1 = daln_df0['text_original'][i]


    s2 =s1.replace(',', '')
    s3 =s2.replace('.', '')
    s4 = re.sub('[\?!:)(«»@#$_1234567890#—ツ►๑۩۞۩•*”˜˜”*°°*`]', '', s3)
    tokens = word_tokenize(s4)
    
    for j in range(0,len(tokens)):
        tokens[j] = morph.parse(tokens[j])[0].normal_form
        doc_stem = doc_stem + tokens[j] + ' '
    

    x_data.append(daln_df0['text_original'][i])
    daln_data.append(doc_stem)

stop = time.time()    
print('time of execution (sec)', stop - start)

time of execution (sec) 138.3401701450348


In [6]:
daln_data

['лидер движение за право человек левый пономарев крайне продуктивно встретиться с представитель японский посольство - попросить деньга за защита японский интерес на дальний восток предложить свой услуга в борьба япония за российский курил и даже похвастаться финансирование от госдеп привет скептик я в свой время высказываться публично что два шикотан и как он хабомая - я считать что мы должный отдать - сказать правозащитник - я считать что если бы россия сделать бы этот шаг вот с хабомая это быть бы правильно японец должный быть заинтересовать именно в гражданский общество там на дальний восток потому что они местный российский правозащитник не быть ангажировать на вот этот гнилой такой патриотизмпонимать то есть там разумный человек и вот вы даже решение проблема остров быть разумный агитировать там обсуждать можно гнилой патриотизм вот как называть правозащитник отстаивание россия свой суверенный территория только надо чтобы грант давать частный фонд японский мы-то американец вообще

In [8]:
# finally, the tf-idf matrix is computed, while stopwords are removed from the text
# I simply used a list of Russian stopwords provided by the this Github repository https://github.com/stopwords-iso/stopwords-ru

file_name ='stopwords-ru.txt'
words1 = pd.read_csv(file_name, header = None)

# transform data to list
my_stop_ru = words1[0].values.tolist()

from sklearn.feature_extraction.text import TfidfVectorizer
vec = TfidfVectorizer(ngram_range=(1,1), stop_words=(my_stop_ru))

# we extract words (calculate tf-idf frequence) and transform data to array
daln_transform = vec.fit_transform(daln_data).toarray()

dmatrix_freq = np.asarray(daln_transform.sum(axis=0)).ravel()
final_dmatrix = np.array([np.array(vec.get_feature_names()), dmatrix_freq])

C:\Users\Asus\Anaconda3\lib\site-packages\sklearn\feature_extraction\text.py:301: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['хотел'] not in stop_words.
  'stop_words.' % sorted(inconsistent))


In [10]:
final_dmatrix #so here how the matrix looks

array([['aaav', 'aami', 'aamiиз', ..., 'ёлочный', 'ёмкость', 'ёмэймона'],
       ['0.01073005523938268', '0.0519691543335623',
        '0.03761396414654988', ..., '0.056278258671507625',
        '0.4083574742575078', '0.052903912982921845']], dtype='<U72')

Now, when I am done with the daln dataset, the same operations can be carried out for the amazon data.

In [12]:
#first, loading the data
amc = pd.read_csv('amazon_cells_labelled.txt', header=None, sep = '\n')
amc.shape #for this dataset we have 1000 rows of text

(1000, 1)

In [13]:
amc0 = amc.rename(columns={amc.columns[0]: "text"}) #here, I also do the renaming of the column with text for my own convinience

In [14]:
amc0.head() #okay, looks good so far

text
0  So there is no way for me to plug it in here i...
1                     Good case, Excellent value.\t1
2                          Great for the jawbone.\t1
3  Tied to charger for conversations lasting more...
4                               The mic is great.\t1

In [16]:
#further, the tokenization and stemming follow

from nltk.stem import PorterStemmer
stemmer = PorterStemmer()

# Create a text cleaning procedure
def clear_data(df):
    df['text'] = df['text'].apply(lambda text: text.strip().split('|')[-1].split('http')[0].strip().lower())
    df['text'] = df['text'].apply(lambda text: re.sub('[?\!«»@#$_@#$1234567890#—ツ►๑۩۞۩•*”˜˜”*°°*``,.]', '', text))
    return df
    
# Creating a procedure for tokenization and data stemming
def tokenize_and_stem(df):
    df['text'] = df['text'].apply(lambda text: word_tokenize(text))
    df['text'] = df['text'].apply(lambda text: [stemmer.stem(word) for word in text])
    df['text'] = df['text'].apply(lambda text: ' '.join(text))
    return df

In [17]:
# We carry out preprocessing
amc_clean = clear_data(amc0)
amc_data = tokenize_and_stem(amc_clean)

amc_data.head()

text
0  so there is no way for me to plug it in here i...
1                               good case excel valu
2                               great for the jawbon
3  tie to charger for convers last more than minu...
4                                   the mic is great

In [18]:
#and list of English stopwords I got from here https://gist.github.com/sebleier/554280
#lastly, a tf-idf matrix can be computed after stopwords are removed

file_stop ='stopwords-en.txt'
words2 = pd.read_csv(file_stop, header = None)

my_stop_en = words2[0].values.tolist()

from sklearn.feature_extraction.text import TfidfVectorizer
vec = TfidfVectorizer(ngram_range=(1,1), stop_words=(my_stop_en))

amc_transform = vec.fit_transform(amc_data['text'].values)

amatrix_freq = np.asarray(amc_transform.sum(axis=0)).ravel()
final_amatrix = np.array([np.array(vec.get_feature_names()), amatrix_freq])

In [19]:
final_amatrix #the matrix itself

array([['abhor', 'abil', 'abl', ..., 'yet', 'za', 'zero'],
       ['0.544595171043447', '0.7454059228688994', '1.6642052933753906',
        ..., '1.2645852895696867', '0.4191655560787057',
        '0.4321410815889337']], dtype='<U32')